# Product Matching

In [1]:
import pandas as pd
import json
import numpy as np
from collections import Counter
import re
import matplotlib.pyplot as plt
import spacy
from spacy import displacy # viz
from spacy.lang.nl.stop_words import STOP_WORDS
import nl_core_news_sm
import string
import time
from datasketch import MinHash, MinHashLSHForest
import pickle

from sklearn.neighbors import NearestNeighbors

import warnings
warnings.simplefilter('ignore')

In [2]:
nlp = nl_core_news_sm.load() # loading Dutch, since data has Dutch descriptions!

# or, alternatively:
#nlp = spacy.load('nl_core_news_sm')

## Importing data

In [3]:
with open(r'data_anon.pkl', 'rb') as f:
    data = pickle.load(f)

In [139]:
data.head(4)

BRAND                                        DESCRIPTION  \
0   Kärcher  De velgenreiniger 'Car & Bike' van Kärcher is ...   
1    Levi's  De matte muurverf Originals potloodgrijs van L...   
2     Rapid  Vlakdraad nieten. Oorspronkelijk ontworpen voo...   
3  Differnz  Toiletmeubel Fabulous 40 is een van de meest v...   

                                            NAME  
0      Kärcher velgenreiniger 'Car & Bike' 0,5 L  
1       Muurverf Originals mat 2,5l potloodgrijs  
2                   Rapid Nieten - No 970 - 8 mm  
3  Differnz Fabulous Fonteinmeubel - 40 cm - Wit

In [7]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 101781 entries, 0 to 101780
Data columns (total 3 columns):
BRAND          76050 non-null object
DESCRIPTION    98122 non-null object
NAME           101781 non-null object
dtypes: object(3)
memory usage: 2.3+ MB


In [8]:
data.isna().mean().round(3) * 100  # % of missing values

BRAND          25.3
DESCRIPTION     3.6
NAME            0.0
dtype: float64

## NLP with spaCy

### Checking an example of tokenization

In [11]:
txt = data.loc[0, 'DESCRIPTION']
doc = nlp(txt)
# Token texts
[token.text for token in doc]

['De',
 'velgenreiniger',
 "'",
 'Car',
 '&',
 'Bike',
 "'",
 'van',
 'Kärcher',
 'is',
 'geschikt',
 'om',
 'remsporen',
 ',',
 'wintervuil',
 'en',
 'ander',
 'straatvuil',
 'van',
 'alle',
 'soorten',
 'wielen',
 'te',
 'kuisen',
 '.',
 'Dankzij',
 'zijn',
 'slimme',
 'kleurverandering',
 'geeft',
 'hij',
 'aan',
 'wanneer',
 'de',
 'wielen',
 'klaar',
 'zijn',
 'om',
 'af',
 'te',
 'spoelen',
 '.']

### Quick viz

In [12]:
displacy.render(doc, style="dep")

# Now, getting into business...

## Concatenating all columns

In [13]:
all_texts = pd.DataFrame(data.apply(lambda x: str(x), axis=1))

In [14]:
all_texts = all_texts.rename(columns={0: 'all_text'})

## Cleaning and standardizing text

### Add stopwords

In [19]:
nlp.Defaults.stop_words |= {'brand',
                            'description',
                            'name',
                            'shop',
                            'dtype object'
                            'nan'
                           }

stopwords = nlp.Defaults.stop_words

### Clean up, filter and standardize (lemmatize) all text

In [88]:
# Clean text before feeding it to spaCy

def clean_string(x):
    x = x.lower()
    x = x.replace('\n', ' ')
    x = re.sub(r'[^\w\s]', '', x)
    x = x.replace('httpswww', '')
    x = x.replace('display_url', '')
    x = x.replace('dtype object', '')
    x = x.replace('inhoud', '')
    x = x.replace('nan', '')
    x = x.replace('none', '')
    
    x = x.rstrip()
    try:
        if isinstance(int(x.split(' ')[-1]), int):
            x = x.split(' ')[:-1]
    except ValueError:
        x = x.split(' ')
    x = ' '.join(x)
    x = x.rstrip()
    return x

punctuations = string.punctuation

# Define function to cleanup text by removing personal pronouns, stopwords and punctuation
def cleanup_text(docs):
    texts = []
    counter = 1
    for doc in docs:
        counter += 1
        doc = nlp(doc, disable=['parser', 'ner']) # disabling parser and NER
        tokens = [tok for tok in doc if tok.pos_ in ['NOUN', 'PROPN', 'ADJ']] # include only these
        tokens = [clean_string(tok.lemma_) for tok in doc if tok.lemma_ != '-PRON-']
        tokens = [tok for tok in tokens if tok not in stopwords and tok not in punctuations]
        tokens = ' '.join(tokens)
        texts.append(tokens)
    return pd.Series(texts)

In [109]:
all_text = [text for text in all_texts['all_text']]

In [110]:
all_text[:2]

["BRAND                                                    Kärcher\nDESCRIPTION    De velgenreiniger 'Car & Bike' van Kärcher is ...\nNAME                   Kärcher velgenreiniger 'Car & Bike' 0,5 L\nName: 0, dtype: object",
 "BRAND                                                     Levi's\nDESCRIPTION    De matte muurverf Originals potloodgrijs van L...\nNAME                    Muurverf Originals mat 2,5l potloodgrijs\nName: 1, dtype: object"]

In [111]:
data_clean_df = pd.DataFrame(cleanup_text(all_text), columns=['all_text'])

In [112]:
data_clean_df['all_text'] = list(map(clean_string, data_clean_df['all_text']))

In [113]:
data_clean_df.head(2).values

array([['kärcher velgenreiniger car bike kärcher naam kärcher velgenreiniger car bike l'],
       ['levi matte muurverf originals potloodgrij l naam muurverf originals mat 25l potloodgrij']],
      dtype=object)

# Using the Locality Sensitive Hashing technique

In [115]:
# preprocess function will split a string of text into individual tokens/shingles based on whitespace

def preprocess(text):
    text = re.sub(r'[^\w\s]','',text)
    tokens = text.lower()
    tokens = tokens.split()
    return tokens

In [116]:
# number of Permutations
permutations = 128 # 128 as standard number

# number of Recommendations to return
num_recommendations = 1

In [117]:
def get_forest(data, perms):
    start_time = time.time()
    
    minhash = []
    
    for text in data['all_text']:
        text = clean_string(text)
        tokens = preprocess(text)
        m = MinHash(num_perm=perms)
        for s in tokens:
            m.update(s.encode('utf8'))
        minhash.append(m)
        
    forest = MinHashLSHForest(num_perm=perms)
    
    for i,m in enumerate(minhash):
        forest.add(i,m)
        
    forest.index()
    
    print('It took %s seconds to build the forest.' %(time.time()-start_time))

    return forest

In [118]:
def predict(text, database, perms, num_results, forest):
    start_time = time.time()
    
    text = clean_string(text)
    tokens = preprocess(text)
    m = MinHash(num_perm=perms)
    for s in tokens:
        m.update(s.encode('utf8'))
        
    idx_array = np.array(forest.query(m, num_results))
    if len(idx_array) == 0:
        return None # if your query is empty, return none
    
    result = database.iloc[idx_array]['all_text']
    
    print('It took %s seconds to query the forest.' %(time.time()-start_time))
    
    return result

In [119]:
forest = get_forest(data_clean_df, permutations)

It took 73.79276013374329 seconds to build the forest.


### testing for one example

In [120]:
num_recommendations = 2
all_text = data_clean_df['all_text'][0]
result = predict(all_text, data_clean_df, permutations, num_recommendations, forest)
print('\n Top Recommendation(s) is(are) \n', result)

It took 0.001997232437133789 seconds to query the forest.

 Top Recommendation(s) is(are) 
 0        kärcher velgenreiniger car bike kärcher naam k...
14333    kärcher kärcher auto shampoo car bike l naam k...
Name: all_text, dtype: object


### loop it for all data!

In [124]:
results_lhs = [predict(text, data_clean_df, permutations, num_recommendations, forest) for text in data_clean_df['all_text']]

It took 0.0019958019256591797 seconds to query the forest.
It took 0.0019948482513427734 seconds to query the forest.
It took 0.001985311508178711 seconds to query the forest.
It took 0.002001523971557617 seconds to query the forest.
It took 0.001983165740966797 seconds to query the forest.
It took 0.03401041030883789 seconds to query the forest.
It took 0.0019969940185546875 seconds to query the forest.
It took 0.003993511199951172 seconds to query the forest.
It took 0.004037380218505859 seconds to query the forest.
It took 0.0019638538360595703 seconds to query the forest.
It took 0.001997709274291992 seconds to query the forest.
It took 0.000986337661743164 seconds to query the forest.
It took 0.0010030269622802734 seconds to query the forest.
It took 0.0019752979278564453 seconds to query the forest.
It took 0.002028942108154297 seconds to query the forest.
It took 0.002013683319091797 seconds to query the forest.
It took 0.003025531768798828 seconds to query the forest.
It took 0

It took 0.0019986629486083984 seconds to query the forest.
It took 0.0020036697387695312 seconds to query the forest.
It took 0.0020172595977783203 seconds to query the forest.
It took 0.0019958019256591797 seconds to query the forest.
It took 0.003004312515258789 seconds to query the forest.
It took 0.0019960403442382812 seconds to query the forest.
It took 0.0009996891021728516 seconds to query the forest.
It took 0.0019986629486083984 seconds to query the forest.
It took 0.0010318756103515625 seconds to query the forest.
It took 0.0020017623901367188 seconds to query the forest.
It took 0.0010006427764892578 seconds to query the forest.
It took 0.001998424530029297 seconds to query the forest.
It took 0.001999378204345703 seconds to query the forest.
It took 0.001998424530029297 seconds to query the forest.
It took 0.0009903907775878906 seconds to query the forest.
It took 0.001995563507080078 seconds to query the forest.
It took 0.0020012855529785156 seconds to query the forest.
It

It took 0.003996849060058594 seconds to query the forest.
It took 0.0019936561584472656 seconds to query the forest.
It took 0.003015279769897461 seconds to query the forest.
It took 0.0010020732879638672 seconds to query the forest.
It took 0.0020074844360351562 seconds to query the forest.
It took 0.0010042190551757812 seconds to query the forest.
It took 0.0010139942169189453 seconds to query the forest.
It took 0.0019855499267578125 seconds to query the forest.
It took 0.0010318756103515625 seconds to query the forest.
It took 0.0019953250885009766 seconds to query the forest.
It took 0.0030031204223632812 seconds to query the forest.
It took 0.0020329952239990234 seconds to query the forest.
It took 0.0009772777557373047 seconds to query the forest.
It took 0.002028942108154297 seconds to query the forest.
It took 0.0020148754119873047 seconds to query the forest.
It took 0.0030014514923095703 seconds to query the forest.
It took 0.0010197162628173828 seconds to query the forest.


It took 0.002996206283569336 seconds to query the forest.
It took 0.0010259151458740234 seconds to query the forest.
It took 0.0010008811950683594 seconds to query the forest.
It took 0.001981973648071289 seconds to query the forest.
It took 0.0020029544830322266 seconds to query the forest.
It took 0.0010008811950683594 seconds to query the forest.
It took 0.0019936561584472656 seconds to query the forest.
It took 0.001975536346435547 seconds to query the forest.
It took 0.002000093460083008 seconds to query the forest.
It took 0.0009965896606445312 seconds to query the forest.
It took 0.0029976367950439453 seconds to query the forest.
It took 0.002015829086303711 seconds to query the forest.
It took 0.0019948482513427734 seconds to query the forest.
It took 0.00201416015625 seconds to query the forest.
It took 0.003992795944213867 seconds to query the forest.
It took 0.0020017623901367188 seconds to query the forest.
It took 0.0019996166229248047 seconds to query the forest.
It took 

It took 0.0029976367950439453 seconds to query the forest.
It took 0.004008054733276367 seconds to query the forest.
It took 0.002000093460083008 seconds to query the forest.
It took 0.0020012855529785156 seconds to query the forest.
It took 0.0020058155059814453 seconds to query the forest.
It took 0.0020012855529785156 seconds to query the forest.
It took 0.0009877681732177734 seconds to query the forest.
It took 0.0039980411529541016 seconds to query the forest.
It took 0.003000497817993164 seconds to query the forest.
It took 0.000982046127319336 seconds to query the forest.
It took 0.002999544143676758 seconds to query the forest.
It took 0.003995180130004883 seconds to query the forest.
It took 0.0020017623901367188 seconds to query the forest.
It took 0.003000497817993164 seconds to query the forest.
It took 0.001997709274291992 seconds to query the forest.
It took 0.0019991397857666016 seconds to query the forest.
It took 0.005988359451293945 seconds to query the forest.
It too

...

It took 0.004002809524536133 seconds to query the forest.
It took 0.0065419673919677734 seconds to query the forest.
It took 0.003431558609008789 seconds to query the forest.
It took 0.004653453826904297 seconds to query the forest.
It took 0.00400090217590332 seconds to query the forest.
It took 0.005986928939819336 seconds to query the forest.
It took 0.003009796142578125 seconds to query the forest.
It took 0.007991552352905273 seconds to query the forest.
It took 0.004007577896118164 seconds to query the forest.
It took 0.0029973983764648438 seconds to query the forest.
It took 0.0020020008087158203 seconds to query the forest.
It took 0.0049855709075927734 seconds to query the forest.
It took 0.0032896995544433594 seconds to query the forest.
It took 0.003003835678100586 seconds to query the forest.
It took 0.003004789352416992 seconds to query the forest.
It took 0.006040334701538086 seconds to query the forest.
It took 0.004000663757324219 seconds to query the forest.
It took 0.

It took 0.0018911361694335938 seconds to query the forest.
It took 0.003021240234375 seconds to query the forest.
It took 0.003354310989379883 seconds to query the forest.
It took 0.003817319869995117 seconds to query the forest.
It took 0.00399470329284668 seconds to query the forest.
It took 0.0043070316314697266 seconds to query the forest.
It took 0.003705263137817383 seconds to query the forest.
It took 0.010776281356811523 seconds to query the forest.
It took 0.0029997825622558594 seconds to query the forest.
It took 0.00189208984375 seconds to query the forest.
It took 0.003142833709716797 seconds to query the forest.
It took 0.001998424530029297 seconds to query the forest.
It took 0.0020074844360351562 seconds to query the forest.
It took 0.0020017623901367188 seconds to query the forest.
It took 0.0019989013671875 seconds to query the forest.
It took 0.002559661865234375 seconds to query the forest.
It took 0.0025086402893066406 seconds to query the forest.
It took 0.00186252

It took 0.0029969215393066406 seconds to query the forest.
It took 0.0027818679809570312 seconds to query the forest.
It took 0.0030052661895751953 seconds to query the forest.
It took 0.0029997825622558594 seconds to query the forest.
It took 0.006007671356201172 seconds to query the forest.
It took 0.0010063648223876953 seconds to query the forest.
It took 0.0041141510009765625 seconds to query the forest.
It took 0.005006074905395508 seconds to query the forest.
It took 0.005005836486816406 seconds to query the forest.
It took 0.003696441650390625 seconds to query the forest.
It took 0.0029954910278320312 seconds to query the forest.
It took 0.002003908157348633 seconds to query the forest.
It took 0.002004384994506836 seconds to query the forest.
It took 0.004108905792236328 seconds to query the forest.
It took 0.003118753433227539 seconds to query the forest.
It took 0.0019922256469726562 seconds to query the forest.
It took 0.0029935836791992188 seconds to query the forest.
It to

It took 0.0031273365020751953 seconds to query the forest.
It took 0.00299072265625 seconds to query the forest.
It took 0.004995584487915039 seconds to query the forest.
It took 0.003112316131591797 seconds to query the forest.
It took 0.005004167556762695 seconds to query the forest.
It took 0.004458904266357422 seconds to query the forest.
It took 0.0030913352966308594 seconds to query the forest.
It took 0.0025873184204101562 seconds to query the forest.
It took 0.002223491668701172 seconds to query the forest.
It took 0.0029904842376708984 seconds to query the forest.
It took 0.0030050277709960938 seconds to query the forest.
It took 0.005159616470336914 seconds to query the forest.
It took 0.0029027462005615234 seconds to query the forest.
It took 0.006003379821777344 seconds to query the forest.
It took 0.002002239227294922 seconds to query the forest.
It took 0.0050048828125 seconds to query the forest.
It took 0.002996206283569336 seconds to query the forest.
It took 0.0069942

It took 0.004000186920166016 seconds to query the forest.
It took 0.0039980411529541016 seconds to query the forest.
It took 0.0039937496185302734 seconds to query the forest.
It took 0.0029981136322021484 seconds to query the forest.
It took 0.0039975643157958984 seconds to query the forest.
It took 0.0038781166076660156 seconds to query the forest.
It took 0.003995180130004883 seconds to query the forest.
It took 0.002990245819091797 seconds to query the forest.
It took 0.004004478454589844 seconds to query the forest.
It took 0.0029954910278320312 seconds to query the forest.
It took 0.002995014190673828 seconds to query the forest.
It took 0.007999420166015625 seconds to query the forest.
It took 0.00699615478515625 seconds to query the forest.
It took 0.00673365592956543 seconds to query the forest.
It took 0.007146120071411133 seconds to query the forest.
It took 0.0029973983764648438 seconds to query the forest.
It took 0.002989530563354492 seconds to query the forest.
It took 0

### first 10 matches

In [125]:
results_lhs[:10]

[0        kärcher velgenreiniger car bike kärcher naam k...
 14333    kärcher kärcher auto shampoo car bike l naam k...
 Name: all_text, dtype: object,
 1        levi matte muurverf originals potloodgrij l na...
 46594    levis matte muurverf originals potloodgrij l n...
 Name: all_text, dtype: object,
 3824    rapid vlakdraad nieten oorspronkelijk ontwerpe...
 2       rapid vlakdraad nieten oorspronkelijk ontwerpe...
 Name: all_text, dtype: object,
 58699    differnz toiletmeubel fabulous meest v naam di...
 3        differnz toiletmeubel fabulous meest v naam di...
 Name: all_text, dtype: object,
 5824    pickup pictogram zelfkleven weerbestendig naam...
 4       pickup pickup pictogram zelfkleven weerbestend...
 Name: all_text, dtype: object,
 27026    krachtig grof polijstmiddel verwijderen naam c...
 5        commandant commandant krachtig polijstpast naa...
 Name: all_text, dtype: object,
 6        sun arts vliegengordijnen zorgen heel zomer v ...
 22679    sun arts vliegengordij

# ideas for possible next steps:



- to use a similarity/distance algorithm between all pairs and, e.g. keep only the highest (if to keep only one match when the goal is, for instance, to look for duplicates)
- or setting a threshold and keeping the pair match(es) when the similarity > threshold

# A less efficient approach with NearestNeighbors

## Calling NearestNeighbors

In [130]:
neig_model = NearestNeighbors(n_neighbors=2) # k = 2, since it will retrieve self-matching plus next best match

### get word vectors

In [131]:
# converts a list of words into their word vectors
def get_word_vectors(words):
    return [nlp(word).vector for word in words]

In [132]:
title_vectors = get_word_vectors(data_clean_df['all_text'][:6])

### Fitting the model

In [133]:
neig_model.fit(title_vectors)

NearestNeighbors(algorithm='auto', leaf_size=30, metric='minkowski',
                 metric_params=None, n_jobs=None, n_neighbors=2, p=2,
                 radius=1.0)

### All versus All! Not efficient at All!

In [134]:
full_ls = []
for text in st_all_txt:
        full_ls.append(neig_model.kneighbors([nlp(text).vector]))

### Extracting index of nearest neighbor

In [135]:
#dist_ls = []
ind_ls = []
for k in full_ls:
    #dist_ls.append(k[0][0][1]) # distances
    ind_ls.append(k[1][0][1])